## EDA

In [37]:
import pandas as pd
from sklearn.preprocessing import OrdinalEncoder
from pandas_profiling import ProfileReport
from sklearn.model_selection import cross_val_score
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
import statistics as st
from sklearn.dummy import DummyClassifier
from catboost import CatBoostClassifier
from sklearn.model_selection import train_test_split
# Loading all the libraries
from sklearn.linear_model import LogisticRegression #For comparison
import matplotlib.pyplot as plt
from tensorflow.keras.optimizers import Adam
from sklearn.ensemble import RandomForestClassifier #Classification, but Hypthothesis: we won't need this because it's not random
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold

from sklearn.dummy import DummyClassifier
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import StandardScaler #For Scaling and Balancing
from sklearn.metrics import confusion_matrix #For False/True Postive and Negative Testing

from tensorflow.keras.applications.resnet import ResNet50
from sklearn.utils import shuffle #shuffling for upsampling
from sklearn.metrics import roc_auc_score #TPR (True Positve Rate) vs FPR (False Positive Rate)
from sklearn.metrics import precision_recall_curve #to graph precision and recall and f1
from tensorflow.keras import Sequential
from tensorflow.keras.layers import Dense
from sklearn.utils import class_weight
from sklearn.svm import SVC
import numpy as np

In [38]:
contract = pd.read_csv('C:/Users/Lorenzo Santos/OneDrive/Desktop/final_provider/final_provider/contract.csv')
internet = pd.read_csv('C:/Users/Lorenzo Santos/OneDrive/Desktop/final_provider/final_provider/internet.csv')
personal = pd.read_csv('C:/Users/Lorenzo Santos/OneDrive/Desktop/final_provider/final_provider/personal.csv')
phone = pd.read_csv('C:/Users/Lorenzo Santos/OneDrive/Desktop/final_provider/final_provider/phone.csv')

In [39]:
contract_report = ProfileReport(contract, title='contract', explorative=True)
contract_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [40]:
internet_report = ProfileReport(internet, title='internet', explorative=True)
internet_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [41]:
personal_report = ProfileReport(personal, title='personal', explorative=True)
personal_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [42]:
phone_report = ProfileReport(phone, title='phone', explorative=True)
phone_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [43]:
first_merge = contract.merge(internet,on='customerID',how='outer')
second_merge = phone.merge(personal,on='customerID',how='outer')
telecom = first_merge.merge(second_merge,on='customerID',how='outer')

In [44]:
telecom_report = ProfileReport(telecom, title='contract', explorative=True)
telecom_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [45]:
#It’s perfectly fine to assume that if a customer was not included in a table, they did not sign up for the service and that should be a category in itself
new_telecom = telecom.fillna('No')
#new_telecom.set_index('customerid')
new_telecom_report = ProfileReport(new_telecom, title='new_telecom', explorative=True)
new_telecom_report



Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [46]:
def low(columns):
    new_columns = []
    for column in columns:
        new_columns.append(column.lower())
    return new_columns

new_telecom.columns = low(list(new_telecom.columns))


binary_columns = ['enddate', 'type', 'paperlessbilling',
       'paymentmethod','internetservice',
       'onlinesecurity', 'onlinebackup', 'deviceprotection', 'techsupport',
       'streamingtv', 'streamingmovies', 'multiplelines', 'gender',
       'seniorcitizen', 'partner', 'dependents']

#Since we have more than binary choices, we should one hot encode and not ordinal encode anyway, 
new_telecom_ohe = pd.get_dummies(new_telecom[binary_columns], drop_first=True)
new_telecom_ohe = new_telecom_ohe.drop(columns=['enddate_2019-11-01 00:00:00',
       'enddate_2019-12-01 00:00:00', 'enddate_2020-01-01 00:00:00'])
#print(list(new_telecom_ohe.columns))

new_telecom_ohe.columns = ['senior_citizen', 'no_end_date', 'month_to_month', 'one_year',
       'paperless_billing', 'credit_card',
       'electronic_check', 'mailed_check',
       'fiber_optic', 'no_internet_service',
       'online_security', 'online_backup', 'device_protection',
       'tech_support', 'streaming_tv', 'streaming_movies',
       'multiple_lines', 'gender_male', 'partner', 'dependents']

new_telecom_ohe_report = ProfileReport(new_telecom_ohe, title='new_telecom', explorative=True)
new_telecom_ohe_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Imbalanced Model Training

In [47]:
features = new_telecom_ohe.drop('no_end_date', axis=1)
target = new_telecom_ohe['no_end_date']


features_train, features_remainder, target_train, target_remainder = train_test_split(features,target, test_size=0.2, random_state=12345)
features_valid, features_test, target_valid, target_test = train_test_split(features_remainder,target_remainder, test_size=0.5, random_state=12345)

### Catboost

In [53]:
cat_features = ['senior_citizen', 'month_to_month', 'one_year',
       'paperless_billing', 'credit_card',
       'electronic_check', 'mailed_check',
       'fiber_optic', 'no_internet_service',
       'online_security', 'online_backup', 'device_protection',
       'tech_support', 'streaming_tv', 'streaming_movies',
       'multiple_lines', 'gender_male', 'partner', 'dependents']

cb = CatBoostClassifier(loss_function="Logloss", iterations=5000)
cb.fit(features_train, target_train, cat_features=cat_features, verbose=100)
print('Logistic Regression Accuracy:', cb.score(features_valid, target_valid))


cb_probabilities_valid = cb.predict_proba(features_valid)
cb_probabilities_one_valid = cb_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression AUC-ROC score:',roc_auc_score(target_valid,cb_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

Learning rate set to 0.004927
0:	learn: 0.6899824	total: 2.02ms	remaining: 10.1s
100:	learn: 0.5120846	total: 200ms	remaining: 9.68s
200:	learn: 0.4592710	total: 448ms	remaining: 10.7s
300:	learn: 0.4381549	total: 691ms	remaining: 10.8s
400:	learn: 0.4272041	total: 923ms	remaining: 10.6s
500:	learn: 0.4199986	total: 1.13s	remaining: 10.2s
600:	learn: 0.4147064	total: 1.43s	remaining: 10.5s
700:	learn: 0.4102703	total: 1.68s	remaining: 10.3s
800:	learn: 0.4064537	total: 1.9s	remaining: 9.96s
900:	learn: 0.4029622	total: 2.13s	remaining: 9.69s
1000:	learn: 0.3995161	total: 2.37s	remaining: 9.46s
1100:	learn: 0.3966577	total: 2.57s	remaining: 9.09s
1200:	learn: 0.3939628	total: 2.78s	remaining: 8.81s
1300:	learn: 0.3912153	total: 3s	remaining: 8.53s
1400:	learn: 0.3887634	total: 3.21s	remaining: 8.25s
1500:	learn: 0.3862190	total: 3.42s	remaining: 7.96s
1600:	learn: 0.3835741	total: 3.67s	remaining: 7.79s
1700:	learn: 0.3811787	total: 3.97s	remaining: 7.7s
1800:	learn: 0.3786942	total: 4.

### Logistic Regression

In [ ]:
lr_model = LogisticRegression(random_state=12345, solver='lbfgs')
lr_model.fit(features_train, target_train)
print('Logistic Regression Accuracy:', lr_model.score(features_valid, target_valid))


lr_probabilities_valid = lr_model.predict_proba(features_valid)
lr_probabilities_one_valid = lr_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression AUC-ROC score:',roc_auc_score(target_valid,lr_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

### Random Forest

In [ ]:
best_rfc_score = 0
best_rfc_est = 0
best_rfc_depth = 0
best_rfc_auc_roc = 0

for depth in range(1,10):
    for est in range(1,20):
        rfc_model = RandomForestClassifier(random_state=12345, n_estimators=est, max_depth=depth)
        rfc_model.fit(features_train, target_train)
        score = rfc_model.score(features_valid, target_valid)
        rfc_probabilities_valid = rfc_model.predict_proba(features_valid)
        rfc_probabilities_one_valid = rfc_probabilities_valid[:,1]
        auc_roc = roc_auc_score(target_valid,rfc_probabilities_one_valid)
    if auc_roc > best_rfc_auc_roc:
            best_rfc_auc_roc = auc_roc
            best_rfc_score = score 
            best_rfc_est = est 
            best_rfc_depth = depth 


print("Accuracy of the best Random Forest Classifier model on the validation set (n_estimators = {}, max_depth = {}): {}".format(best_rfc_est, best_rfc_depth ,best_rfc_score))
print('Random Forest Classifier AUC-ROC score:',best_rfc_auc_roc) #TPR (True Positve Rate) vs FPR (False Positive Rate)

### Neural Network

Note: This one will take a while, please wait.

In [14]:
#Had to convert neural networks on non image data.
#https://machinelearningmastery.com/tutorial-first-neural-network-python-keras/

#print(features_train.shape)



nn_model = Sequential()
nn_model.add(Dense(1000, input_shape=(3251,19), activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
#sigmoid for binary (2d) classification:
nn_model.add(Dense(1, activation='sigmoid'))

optimizer = Adam(learning_rate=0.000001) #lr is depreciated

nn_model.compile(
    #Binary crossentropy according to the database for best AUC score
    loss='binary_crossentropy', optimizer=optimizer,metrics=['acc','AUC']) #AUC has ROC curve included according to documentation.

nn = nn_model.fit(
    features_train,
    target_train,
    validation_data=(features_valid, target_valid),
    epochs=309,
    verbose=2,
    steps_per_epoch=150,
    batch_size=32
)



nn_model.summary()



#predict_proba is depreciated 

Epoch 1/309
150/150 - 2s - loss: 0.6796 - acc: 0.6862 - auc: 0.4976 - val_loss: 0.6650 - val_acc: 0.7358 - val_auc: 0.5514
Epoch 2/309
150/150 - 1s - loss: 0.6512 - acc: 0.7386 - auc: 0.5872 - val_loss: 0.6402 - val_acc: 0.7358 - val_auc: 0.6200
Epoch 3/309
150/150 - 1s - loss: 0.6295 - acc: 0.7314 - auc: 0.6413 - val_loss: 0.6188 - val_acc: 0.7358 - val_auc: 0.6500
Epoch 4/309
150/150 - 1s - loss: 0.6084 - acc: 0.7333 - auc: 0.6790 - val_loss: 0.6001 - val_acc: 0.7358 - val_auc: 0.6725
Epoch 5/309
150/150 - 1s - loss: 0.5905 - acc: 0.7365 - auc: 0.6883 - val_loss: 0.5839 - val_acc: 0.7358 - val_auc: 0.6898
Epoch 6/309
150/150 - 1s - loss: 0.5753 - acc: 0.7367 - auc: 0.7085 - val_loss: 0.5697 - val_acc: 0.7358 - val_auc: 0.7122
Epoch 7/309
150/150 - 1s - loss: 0.5625 - acc: 0.7342 - auc: 0.7346 - val_loss: 0.5576 - val_acc: 0.7358 - val_auc: 0.7297
Epoch 8/309
150/150 - 1s - loss: 0.5487 - acc: 0.7379 - auc: 0.7514 - val_loss: 0.5469 - val_acc: 0.7358 - val_auc: 0.7469
Epoch 9/309
150/

KeyboardInterrupt: 

In [ ]:
#https://stackoverflow.com/questions/49873676/how-to-calculate-the-average-of-training-accuracy-in-keras
#https://datagy.io/python-index-of-max-item-list/

print('At',nn.history['val_acc'].index(max(nn.history['val_acc'])),'epochs we have an accuracy of:',max(nn.history['val_acc']))
print('At',nn.history['val_auc'].index(max(nn.history['val_auc'])),'epochs we have an MAX AUC_ROC of:',max(nn.history['val_auc']))

### Support Vector Machine

In [ ]:
#https://www.discoverbits.in/371/sklearn-attributeerror-predict_proba-available-probability

svm = SVC(kernel='linear',probability=True)
svm.fit(features_train,target_train)
print('Support Vector Machine Accuracy:', svm.score(features_valid, target_valid))


svm_probabilities_valid = svm.predict_proba(features_valid)
svm_probabilities_one_valid = svm_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Support Vector Machine Regression AUC-ROC score:',roc_auc_score(target_valid,svm_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

### Dummy Classifier (Sanity Check)

In [ ]:
dummy = DummyClassifier(strategy="most_frequent")
dummy.fit(features_train,target_train)

dummy_probabilities_valid = dummy.predict_proba(features_valid)
dummy_probabilities_one_valid = dummy_probabilities_valid[:,1]
print('Dummy Regression AUC-ROC score:',roc_auc_score(target_valid,dummy_probabilities_one_valid)) 
print('Accuracy:', dummy.score(features_valid,target_valid))

## Balanced Model Training

Logistic Regression has the highest AUC-ROC score. There also isn't 10x more 0s than ones. More like 4.

### Upsampled

In [ ]:
def upsample(features, target, repeat):
    features_zeros = features[target == 0]
    features_ones = features[target == 1]
    target_zeros = target[target == 0]
    target_ones = target[target == 1]

    features_upsampled = pd.concat([features_zeros] + [features_ones] * repeat)
    target_upsampled = pd.concat([target_zeros] + [target_ones] * repeat)

    features_upsampled, target_upsampled = shuffle(
        features_upsampled, target_upsampled, random_state=12345
    )

    return features_upsampled, target_upsampled


features_upsampled, target_upsampled = upsample(
    features_train, target_train, 4
)

#### Logistic Regression

In [ ]:
lr_model = LogisticRegression(random_state=12345, solver='lbfgs')
lr_model.fit(features_upsampled, target_upsampled)
print('Logistic Regression Accuracy:', lr_model.score(features_valid, target_valid))


lr_probabilities_valid = lr_model.predict_proba(features_valid)
lr_probabilities_one_valid = lr_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression Upsampled AUC-ROC score:',roc_auc_score(target_valid,lr_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Random Forest Classifier

In [ ]:
best_rfc_score = 0
best_rfc_est = 0
best_rfc_depth = 0
best_rfc_auc_roc = 0

for depth in range(1,10):
    for est in range(1,20):
        rfc_model = RandomForestClassifier(random_state=12345, n_estimators=est, max_depth=depth)
        rfc_model.fit(features_upsampled, target_upsampled)
        score = rfc_model.score(features_valid, target_valid)
        rfc_probabilities_valid = rfc_model.predict_proba(features_valid)
        rfc_probabilities_one_valid = rfc_probabilities_valid[:,1]
        auc_roc = roc_auc_score(target_valid,rfc_probabilities_one_valid)
    if auc_roc > best_rfc_auc_roc:
            best_rfc_auc_roc = auc_roc
            best_rfc_score = score 
            best_rfc_est = est 
            best_rfc_depth = depth 


print("Accuracy of the best Random Forest Classifier model on the validation set (n_estimators = {}, max_depth = {}): {}".format(best_rfc_est, best_rfc_depth ,best_rfc_score))
print('Random Forest Classifier AUC-ROC score:',best_rfc_auc_roc) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Neural Network

In [ ]:
#Had to convert neural networks on non image data.
#https://machinelearningmastery.com/tutorial-first-neural-network-python-keras/

#print(features_train.shape)



nn_model = Sequential()
nn_model.add(Dense(1000, input_shape=(3251,19), activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
#sigmoid for binary (2d) classification:
nn_model.add(Dense(1, activation='sigmoid'))

optimizer = Adam(learning_rate=0.000001) #lr is depreciated

nn_model.compile(
    #Binary crossentropy according to the database for best AUC score
    loss='binary_crossentropy', optimizer=optimizer,metrics=['acc','AUC']) #AUC has ROC curve included according to documentation.

nn = nn_model.fit(
    features_upsampled,
    target_upsampled,
    validation_data=(features_valid, target_valid),
    epochs=309,
    verbose=2,
    steps_per_epoch=150,
    batch_size=32
)



nn_model.summary()



#predict_proba is depreciated 

In [ ]:
#https://stackoverflow.com/questions/49873676/how-to-calculate-the-average-of-training-accuracy-in-keras
#https://datagy.io/python-index-of-max-item-list/

print('At',nn.history['val_auc'].index(max(nn.history['val_auc'])),'epochs we have an MAX AUC_ROC of:',max(nn.history['val_auc']))
print('At',nn.history['val_acc'].index(max(nn.history['val_acc'])),'epochs we have an accuracy of:',max(nn.history['val_acc']))

#### Support Vector Machine

In [ ]:
#https://www.discoverbits.in/371/sklearn-attributeerror-predict_proba-available-probability

svm = SVC(kernel='linear',probability=True)
svm.fit(features_upsampled, target_upsampled)
print('Support Vector Machine Accuracy:', svm.score(features_valid, target_valid))


svm_probabilities_valid = svm.predict_proba(features_valid)
svm_probabilities_one_valid = svm_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Support Vector Machine Regression AUC-ROC score:',roc_auc_score(target_valid,svm_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Dummy Classifier(Sanity Check)

In [ ]:
dummy = DummyClassifier(strategy="most_frequent")
dummy.fit(features_upsampled, target_upsampled)

dummy_probabilities_valid = dummy.predict_proba(features_valid)
dummy_probabilities_one_valid = dummy_probabilities_valid[:,1]
print('Dummy Regression AUC-ROC score:',roc_auc_score(target_valid,dummy_probabilities_one_valid)) 
print('Accuracy:', dummy.score(features_valid,target_valid))

### Downsampling

In [ ]:
def downsample(features, target, fraction):
    features_zeros = features[target == 0]
    features_ones = features[target == 1]
    target_zeros = target[target == 0]
    target_ones = target[target == 1]

    features_downsampled = pd.concat(
        [features_zeros.sample(frac=fraction, random_state=54321)] + [features_ones])
    target_downsampled = pd.concat(
        [target_zeros.sample(frac=fraction, random_state=54321)] + [target_ones])

    features_downsampled, target_downsampled = shuffle(
        features_downsampled, target_downsampled, random_state=54321)

    return features_downsampled, target_downsampled


features_downsampled, target_downsampled = downsample(
    features_train, target_train, 0.25
)

#### Logistic Regression

In [ ]:
lr_model = LogisticRegression(random_state=12345, solver='lbfgs')
lr_model.fit(features_downsampled, target_downsampled)
print('Logistic Regression Accuracy:', lr_model.score(features_valid, target_valid))


lr_probabilities_valid = lr_model.predict_proba(features_valid)
lr_probabilities_one_valid = lr_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression Downsampled AUC-ROC score:',roc_auc_score(target_valid,lr_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Random Forest Classifier

In [ ]:
best_rfc_score = 0
best_rfc_est = 0
best_rfc_depth = 0
best_rfc_auc_roc = 0

for depth in range(1,10):
    for est in range(1,20):
        rfc_model = RandomForestClassifier(random_state=12345, n_estimators=est, max_depth=depth)
        rfc_model.fit(features_downsampled, target_downsampled)
        score = rfc_model.score(features_valid, target_valid)
        rfc_probabilities_valid = rfc_model.predict_proba(features_valid)
        rfc_probabilities_one_valid = rfc_probabilities_valid[:,1]
        auc_roc = roc_auc_score(target_valid,rfc_probabilities_one_valid)
    if auc_roc > best_rfc_auc_roc:
            best_rfc_auc_roc = auc_roc
            best_rfc_score = score 
            best_rfc_est = est 
            best_rfc_depth = depth 


print("Accuracy of the best Random Forest Classifier model on the validation set (n_estimators = {}, max_depth = {}): {}".format(best_rfc_est, best_rfc_depth ,best_rfc_score))
print('Random Forest Classifier AUC-ROC score:',best_rfc_auc_roc) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Neural Network

In [ ]:
#Had to convert neural networks on non image data.
#https://machinelearningmastery.com/tutorial-first-neural-network-python-keras/

#print(features_train.shape)



nn_model = Sequential()
nn_model.add(Dense(1000, input_shape=(3251,19), activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
#sigmoid for binary (2d) classification:
nn_model.add(Dense(1, activation='sigmoid'))

optimizer = Adam(learning_rate=0.000001) #lr is depreciated

nn_model.compile(
    #Binary crossentropy according to the database for best AUC score
    loss='binary_crossentropy', optimizer=optimizer,metrics=['acc','AUC']) #AUC has ROC curve included according to documentation.

nn = nn_model.fit(
    features_downsampled, 
    target_downsampled,
    validation_data=(features_valid, target_valid),
    epochs=309,
    verbose=2,
    steps_per_epoch=150,
    batch_size=32
)



nn_model.summary()



#predict_proba is depreciated 

In [ ]:
#https://stackoverflow.com/questions/49873676/how-to-calculate-the-average-of-training-accuracy-in-keras
#https://datagy.io/python-index-of-max-item-list/

print('At',nn.history['val_auc'].index(max(nn.history['val_auc'])),'epochs we have an MAX AUC_ROC of:',max(nn.history['val_auc']))
print('At',nn.history['val_acc'].index(max(nn.history['val_acc'])),'epochs we have an accuracy of:',max(nn.history['val_acc']))

#### Support Vector Machine

In [ ]:
#https://www.discoverbits.in/371/sklearn-attributeerror-predict_proba-available-probability

svm = SVC(kernel='linear',probability=True)
svm.fit(features_downsampled, target_downsampled)
print('Support Vector Machine Accuracy:', svm.score(features_valid, target_valid))


svm_probabilities_valid = svm.predict_proba(features_valid)
svm_probabilities_one_valid = svm_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Support Vector Machine Regression AUC-ROC score:',roc_auc_score(target_valid,svm_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Dummy Classifier(Sanity Check)

In [ ]:
dummy = DummyClassifier(strategy="most_frequent")
dummy.fit(features_downsampled, target_downsampled)

dummy_probabilities_valid = dummy.predict_proba(features_valid)
dummy_probabilities_one_valid = dummy_probabilities_valid[:,1]
print('Dummy Regression AUC-ROC score:',roc_auc_score(target_valid,dummy_probabilities_one_valid)) 
print('Accuracy:', dummy.score(features_valid,target_valid))

### Balanced

#### Logistic Regression

In [ ]:
lr_model = LogisticRegression(random_state=12345, solver='lbfgs', class_weight='balanced')
lr_model.fit(features_train, target_train)
print('Logistic Regression Accuracy:', lr_model.score(features_valid, target_valid))


lr_probabilities_valid = lr_model.predict_proba(features_valid)
lr_probabilities_one_valid = lr_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression Balenced AUC-ROC score:',roc_auc_score(target_valid,lr_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Random Forest Classifier

In [ ]:
best_rfc_score = 0
best_rfc_est = 0
best_rfc_depth = 0
best_rfc_auc_roc = 0

for depth in range(1,10):
    for est in range(1,20):
        rfc_model = RandomForestClassifier(random_state=12345, n_estimators=est, max_depth=depth, class_weight='balanced')
        rfc_model.fit(features_train, target_train)
        score = rfc_model.score(features_valid, target_valid)
        rfc_probabilities_valid = rfc_model.predict_proba(features_valid)
        rfc_probabilities_one_valid = rfc_probabilities_valid[:,1]
        auc_roc = roc_auc_score(target_valid,rfc_probabilities_one_valid)
    if auc_roc > best_rfc_auc_roc:
            best_rfc_auc_roc = auc_roc
            best_rfc_score = score 
            best_rfc_est = est 
            best_rfc_depth = depth 


print("Accuracy of the best Random Forest Classifier model on the validation set (n_estimators = {}, max_depth = {}): {}".format(best_rfc_est, best_rfc_depth ,best_rfc_score))
print('Random Forest Classifier AUC-ROC score:',best_rfc_auc_roc) #TPR (True Positve Rate) vs FPR (False Positive Rate)

#### Neural Network

In [ ]:
class_weight = {0: 1.,
                1: 2.,
                2: 0.5}

nn_model = Sequential()
nn_model.add(Dense(1000, input_shape=(3251,19), activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
nn_model.add(Dense(1000, activation='relu'))
#sigmoid for binary (2d) classification:
nn_model.add(Dense(1, activation='sigmoid'))

optimizer = Adam(learning_rate=0.000001) #lr is depreciated

nn_model.compile(
    #Binary crossentropy according to the database for best AUC score
    loss='binary_crossentropy', optimizer=optimizer,metrics=['acc','AUC']) #AUC has ROC curve included according to documentation.

nn = nn_model.fit(
    features_train,
    target_train, 
    validation_data=(features_valid, target_valid),
    epochs=309,
    verbose=2,
    steps_per_epoch=150,
    batch_size=32,
    class_weight=class_weight
)



nn_model.summary()



In [ ]:
#https://stackoverflow.com/questions/49873676/how-to-calculate-the-average-of-training-accuracy-in-keras
#https://datagy.io/python-index-of-max-item-list/

print('At',nn.history['val_auc'].index(max(nn.history['val_auc'])),'epochs we have an MAX AUC_ROC of:',max(nn.history['val_auc']))
print('At',nn.history['val_acc'].index(max(nn.history['val_acc'])),'epochs we have an accuracy of:',max(nn.history['val_acc']))

#### Support Vector Machine

In [ ]:
#https://www.discoverbits.in/371/sklearn-attributeerror-predict_proba-available-probability

svm = SVC(kernel='linear',probability=True,class_weight='balanced')
svm.fit(features_train, target_train)
print('Support Vector Machine Accuracy:', svm.score(features_valid, target_valid))


svm_probabilities_valid = svm.predict_proba(features_valid)
svm_probabilities_one_valid = svm_probabilities_valid[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Support Vector Machine Regression AUC-ROC score:',roc_auc_score(target_valid,svm_probabilities_one_valid)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

# Testing

In [ ]:
lr_model = LogisticRegression(random_state=12345, solver='lbfgs', class_weight='balanced')
lr_model.fit(features_upsampled, target_upsampled)
print('Logistic Regression Accuracy:', lr_model.score(features_test, target_test))


lr_probabilities_test = lr_model.predict_proba(features_test)
lr_probabilities_one_test = lr_probabilities_test[:,1]
#Unlike other metrics, it takes class "1" probabilities instead of predictions:
print('Logistic Regression Upscaled Balanced AUC-ROC score:',roc_auc_score(target_test,lr_probabilities_one_test)) #TPR (True Positve Rate) vs FPR (False Positive Rate)

Target feature: the `'EndDate'` column equals `'No'`.

Primary metric: AUC-ROC.

Additional metric: Accuracy.

Assessment criteria:

- AUC-ROC < 0.75 — 0 SP
- 0.75 ≤ AUC-ROC < 0.81 — 4 SP
- 0.81 ≤ AUC-ROC < 0.85 — 4.5 SP
- 0.85 ≤ AUC-ROC < 0.87 — 5 SP
- 0.87 ≤ AUC-ROC < 0.88 — 5.5 SP
- AUC-ROC ≥ 0.88 — 6 SP